In [1]:
import geopandas as gpd
# import descartes # don't need to import according to the vid
# https://www.youtube.com/watch?v=RoeVPBVbscQ


import matplotlib.pyplot as plt
import pandas as pd
import reverse_geocoder as rg

from shapely.geometry import Point

from geopandas.tools import sjoin
from geopandas import GeoDataFrame
import geopy.distance

import folium

In [2]:
# Downloaded from FCC's website
## Relevant pages...
# https://us-fcc.box.com/s/f220avmxeun345o6gzr7rwcnp1wslocf
# https://fcc.maps.arcgis.com/apps/webappviewer/index.html?id=6c1b2e73d9d749cdb7bc88a0d1bdd25b
# https://us-fcc.app.box.com/s/f220avmxeun345o6gzr7rwcnp1wslocf

# Verizon coverage map data from FCC just has a long list of counties as multipolygons with no labels or metadata. 
* I decided to reverse geocode based on a coordinate from each of the county multipolygons
* I first found the centroid from each record

* Note: Data last updated May 15, 2021

# Try to find location for each multipolygon by using a point or lat/long coordinate in a reverse geo search

In [3]:
gdf = gpd.read_file('D:\Fast AI 2022\Chapter 2\Random Project Ideas\Phone Coverage\Verizon Voice\Verizon_Wireless_349888.shp')

In [4]:
# Using centroid by itself throws a warning:
#     UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.
# gdf['geometry'].centroid



# Instead, project the shapes onto a flat surface, which can then be used to find the centroid, 
# and then convert back into the original coordinate system.
# https://gis.stackexchange.com/questions/372564/userwarning-when-trying-to-get-centroid-from-a-polygon-geopandas

# df1.to_crs('+proj=cea').centroid.to_crs(df1.crs)

verizon_centroids = gdf['geometry'].to_crs('+proj=cea').centroid.to_crs(gdf['geometry'].crs)
verizon_centroids

0        POINT (-86.64258 32.53479)
1        POINT (-87.72391 30.72219)
2        POINT (-85.39277 31.86882)
3        POINT (-87.12123 33.00098)
4        POINT (-86.56728 33.98073)
                   ...             
3125    POINT (-108.86996 41.65686)
3126    POINT (-110.67179 43.96550)
3127    POINT (-110.55644 41.29478)
3128    POINT (-107.70929 43.91980)
3129    POINT (-104.57189 43.84475)
Length: 3130, dtype: geometry

In [5]:
lon = verizon_centroids[0].x
lat = verizon_centroids[0].y

In [6]:
# Function to reverse geocode based on lat/long coordinates
def reverseGeocode(coordinates):
    result = rg.search(coordinates)
    return result
 


In [ ]:
# ## Attempting to reverse geocode all of the centroids for all counties in the verizon coverage maps
# locations = [reverseGeocode((centroid.y,centroid.x)) for centroid in verizon_centroids]

# After attempting to reverse geocode the whole list, I found this process was very slow.
* Since this is just a proof of concept, and I only want to try one example; I am limiting the reverse geocoding to New Hampshire.
* I noticed the counties were in alphabetical order by state then county, and found the first county listed in New Hampshire.
* I used a while loop to label all of the counties in NH stop when reverse geocode no longer returns 'New Hampshire' as the state.

In [ ]:
# Check how slow the reverse geocoder is
# it takes close to a second to reverse geocode each record
# There are 3130 records in the dataset
# It will take close to an hour to geocode all counties. I will 

%%timeit 
reverseGeocode((verizon_centroids[600].y,verizon_centroids[600].x))

In [ ]:
# It will take close to an hour to geocode all counties. (3130/.931)/60 = 56.033 minutes
# At some point, I will reverse geocode the whole dataset and save the output as a csv file
(3130/.9)/60

In [7]:
# Starting index for centroids in NH
i = 1752
# List to save the index for each centroid to reference later when getting Verizon coverage maps for NH counties
idx = []
# List to save the reverse geocoded info
NH_counties = []

# While loop to continue to loop until the results are no longer for NH
while reverseGeocode((verizon_centroids[i].y,verizon_centroids[i].x))[0]['admin1'] =='New Hampshire':
    # Save index
    idx.append(i) 
    # reverse geocode to get NH counties of centroid coordinates from verizon coverage maps
    NH_counties.append(reverseGeocode((verizon_centroids[i].y,verizon_centroids[i].x))[0]['admin2'])
    # increase index by one each loop
    i+=1 

# combine index list and counties list into pandas dataframe
nh_cent_df = pd.DataFrame(list(zip(idx,NH_counties)), columns=['idx_num','county'])
                          
nh_cent_df

Loading formatted geocoded file...


idx_num               county
0     1752       Belknap County
1     1753       Carroll County
2     1754      Cheshire County
3     1755          Coos County
4     1756       Grafton County
5     1757  Hillsborough County
6     1758     Merrimack County
7     1759    Rockingham County
8     1760     Strafford County
9     1761      Sullivan County

# Trying to check Hancock Trail route against verizon coverage map for Grafton County

In [13]:

# https://www.alltrails.com/explore/recording/baldwin-county-trail-running-f8bf09f
HancockDF  = pd.read_csv(r'D:\Fast AI 2022\Chapter 2\Random Project Ideas\Phone Coverage\Hancock Trail NH.csv')

In [14]:
HancockDF.shape

(4121, 3)

In [16]:
# Turn lat long from the hiking route into points to join to the verizon coverage map
HancockDF['geometry'] = [Point(xy) for xy in zip(HancockDF['Longitude'], HancockDF['Latitude'])]
HancockDF.head()

Latitude  Longitude  Elevation                    geometry
0  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)
1  44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)
2  44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)
3  44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)
4  44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)

In [17]:
# point = geopandas.GeoDataFrame.from_file('points.shp') 
# poly  = geopandas.GeoDataFrame.from_file('multipol.shp')


point = GeoDataFrame(HancockDF['geometry'], crs="EPSG:4326")
poly = GeoDataFrame(gdf[1756:1757]['geometry'], crs="EPSG:4326") # Get the multipolygon geometry for Grafton County, NH

In [18]:
# Check if points are in multipolygon using left join - 
# right side will be null if those points on the hiking route are not in coverage
pointInPolys = sjoin(point, poly, how='left')
grouped = pointInPolys.groupby('index_right')
list(grouped)

[(1756.0,
                          geometry  index_right
  0     POINT (-71.52360 44.04123)       1756.0
  1     POINT (-71.52357 44.04123)       1756.0
  2     POINT (-71.52360 44.04124)       1756.0
  3     POINT (-71.52364 44.04127)       1756.0
  4     POINT (-71.52368 44.04127)       1756.0
  ...                          ...          ...
  4116  POINT (-71.52384 44.04126)       1756.0
  4117  POINT (-71.52381 44.04127)       1756.0
  4118  POINT (-71.52366 44.04128)       1756.0
  4119  POINT (-71.52362 44.04126)       1756.0
  4120  POINT (-71.52360 44.04123)       1756.0
  
  [3146 rows x 2 columns])]

In [19]:
# Check how many records are out of coverage
pointInPolys['index_right'].isna().sum()

975

In [48]:
# Join back to the hiking route
graft_merge = HancockDF.merge(pointInPolys, left_index=True, right_index=True)
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y  index_right  
0     POINT (-71.52360 44.04123)       1756.0  
1     POINT (-71.52357 44.04123)       1756.0  
2     POINT (-71.52360 44.04124)       1756.0  
3     POINT (-71.52364 44.04127)       1756.0  
4     POINT (-71.52368 44.04127)       1756.0  
...                          ...          ...  
4116  POINT (-71.52384 44.04126)       1756.0  
4117  POINT (-71.52381 44.04127)       1756.0  
4118  POINT (-71.52366 44.04128)       1756.0  
4119  POINT (-71.52362 44.04126)       1756.0  
4120  POINT (-71.52360 44.04123)       1756.0  

[4121 rows x 6 columns]

In [49]:
# Create a lat_long col of tuples of lats/longs to use with geopy.distance
graft_merge['start_lat_long'] = list(zip(graft_merge['Latitude'], graft_merge['Longitude']))
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y  index_right         start_lat_long  
0     POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)  
1     POINT (-71.52357 44.04123)       1756.0  (44.04123, -71.52357)  
2     POINT (-71.52360 44.04124)       1756.0   (44.04124, -71.5236)  
3     POINT (-71.52364 44.04127)       1756.0  (44.04127, -71.52364)  
4     POINT (-71.52368 44.04127)       1756.0  (44.04127, -71.52368)  
...                          ...          ...                    ...  
4116  POINT (-71.52384 44.04126)       1756.0  (44.04126, -71.52384)  
4117  POINT (-71.52381 44.04127)       1756.0  (44.04127, -71.52381)  
4118  POINT (-71.52366 44.04128)       1756.0  (44.04128, -71.52366)  
4119  POINT (-71.52362 44.04126)       1756.0  (44.04126, -71.52362)  
4120  POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)  

[4121 rows x 7 columns]

In [50]:
# Lag the lat_long tuple so there is a tuple for the start of row and the end of the row
graft_merge['end_lat_long'] = graft_merge['start_lat_long'].shift(-1)
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y  index_right         start_lat_long  \
0     POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)       1756.0  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)       1756.0   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)       1756.0  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)       1756.0  (44.04127, -71.52368)   
...                          ...          ...                    ...   
4116  POINT (-71.52384 44.04126)       1756.0  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)       1756.0  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)       1756.0  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)       1756.0  (44.04126, -71.52362)   
4120  POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)   

               end_lat_long  
0     (44.04123, -71.52357)  
1      (44.04124, -71.5236)  
2     (44.04127, -71.52364)  
3     (44.04127, -71.52368)  
4     (44.04127, -71.52373)  
...                     ...  
4116  (44.04127, -71.52381)  
4117  (44.04128, -71.52366)  
4118  (44.04126, -71.52362)  
4119   (44.04123, -71.5236)  
4120                   None  

[4121 rows x 8 columns]

In [51]:
# Create a binary column to show if the that point on the route is in coverage
graft_merge['start_coverage'] = graft_merge['index_right'].apply(lambda x: 0 if pd.isna(x) else 1)
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y  index_right         start_lat_long  \
0     POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)       1756.0  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)       1756.0   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)       1756.0  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)       1756.0  (44.04127, -71.52368)   
...                          ...          ...                    ...   
4116  POINT (-71.52384 44.04126)       1756.0  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)       1756.0  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)       1756.0  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)       1756.0  (44.04126, -71.52362)   
4120  POINT (-71.52360 44.04123)       1756.0   (44.04123, -71.5236)   

               end_lat_long  start_coverage  
0     (44.04123, -71.52357)               1  
1      (44.04124, -71.5236)               1  
2     (44.04127, -71.52364)               1  
3     (44.04127, -71.52368)               1  
4     (44.04127, -71.52373)               1  
...                     ...             ...  
4116  (44.04127, -71.52381)               1  
4117  (44.04128, -71.52366)               1  
4118  (44.04126, -71.52362)               1  
4119   (44.04123, -71.5236)               1  
4120                   None               1  

[4121 rows x 9 columns]

In [52]:
# Drop the index right column that was originally used to check for nulls
graft_merge= graft_merge.drop(columns= ['index_right'])
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y         start_lat_long  \
0     POINT (-71.52360 44.04123)   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)  (44.04127, -71.52368)   
...                          ...                    ...   
4116  POINT (-71.52384 44.04126)  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)  (44.04126, -71.52362)   
4120  POINT (-71.52360 44.04123)   (44.04123, -71.5236)   

               end_lat_long  start_coverage  
0     (44.04123, -71.52357)               1  
1      (44.04124, -71.5236)               1  
2     (44.04127, -71.52364)               1  
3     (44.04127, -71.52368)               1  
4     (44.04127, -71.52373)               1  
...                     ...             ...  
4116  (44.04127, -71.52381)               1  
4117  (44.04128, -71.52366)               1  
4118  (44.04126, -71.52362)               1  
4119   (44.04123, -71.5236)               1  
4120                   None               1  

[4121 rows x 8 columns]

In [53]:
# Lag the coverage column to show if that row is in coverage at the start and end of that point
graft_merge['end_coverage'] = graft_merge['start_coverage'].shift(-1)
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   
4120  44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   

                      geometry_y         start_lat_long  \
0     POINT (-71.52360 44.04123)   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)  (44.04127, -71.52368)   
...                          ...                    ...   
4116  POINT (-71.52384 44.04126)  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)  (44.04126, -71.52362)   
4120  POINT (-71.52360 44.04123)   (44.04123, -71.5236)   

               end_lat_long  start_coverage  end_coverage  
0     (44.04123, -71.52357)               1           1.0  
1      (44.04124, -71.5236)               1           1.0  
2     (44.04127, -71.52364)               1           1.0  
3     (44.04127, -71.52368)               1           1.0  
4     (44.04127, -71.52373)               1           1.0  
...                     ...             ...           ...  
4116  (44.04127, -71.52381)               1           1.0  
4117  (44.04128, -71.52366)               1           1.0  
4118  (44.04126, -71.52362)               1           1.0  
4119   (44.04123, -71.5236)               1           1.0  
4120                   None               1           NaN  

[4121 rows x 9 columns]

In [54]:
# drop any rows that have a null end_lat_long - This is just the last point on the route
graft_merge = graft_merge.dropna()
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4115  44.04126  -71.52389      654.0  POINT (-71.52389 44.04126)   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   

                      geometry_y         start_lat_long  \
0     POINT (-71.52360 44.04123)   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)  (44.04127, -71.52368)   
...                          ...                    ...   
4115  POINT (-71.52389 44.04126)  (44.04126, -71.52389)   
4116  POINT (-71.52384 44.04126)  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)  (44.04126, -71.52362)   

               end_lat_long  start_coverage  end_coverage  
0     (44.04123, -71.52357)               1           1.0  
1      (44.04124, -71.5236)               1           1.0  
2     (44.04127, -71.52364)               1           1.0  
3     (44.04127, -71.52368)               1           1.0  
4     (44.04127, -71.52373)               1           1.0  
...                     ...             ...           ...  
4115  (44.04126, -71.52384)               1           1.0  
4116  (44.04127, -71.52381)               1           1.0  
4117  (44.04128, -71.52366)               1           1.0  
4118  (44.04126, -71.52362)               1           1.0  
4119   (44.04123, -71.5236)               1           1.0  

[4120 rows x 9 columns]

In [55]:
# Adding Distance traveled this step in meters
graft_merge = graft_merge.copy()
graft_merge['step_length'] = graft_merge.apply(lambda x: geopy.distance.geodesic(x.start_lat_long,x.end_lat_long).m, axis=1)

# Adding cumulative distance traveled for the hiking route as a column
graft_merge['dist_traveled'] = graft_merge['step_length'].cumsum()
graft_merge

Latitude  Longitude  Elevation                  geometry_x  \
0     44.04123  -71.52360      655.0   POINT (-71.5236 44.04123)   
1     44.04123  -71.52357      655.0  POINT (-71.52357 44.04123)   
2     44.04124  -71.52360      655.0   POINT (-71.5236 44.04124)   
3     44.04127  -71.52364      655.0  POINT (-71.52364 44.04127)   
4     44.04127  -71.52368      655.0  POINT (-71.52368 44.04127)   
...        ...        ...        ...                         ...   
4115  44.04126  -71.52389      654.0  POINT (-71.52389 44.04126)   
4116  44.04126  -71.52384      654.0  POINT (-71.52384 44.04126)   
4117  44.04127  -71.52381      654.0  POINT (-71.52381 44.04127)   
4118  44.04128  -71.52366      655.0  POINT (-71.52366 44.04128)   
4119  44.04126  -71.52362      655.0  POINT (-71.52362 44.04126)   

                      geometry_y         start_lat_long  \
0     POINT (-71.52360 44.04123)   (44.04123, -71.5236)   
1     POINT (-71.52357 44.04123)  (44.04123, -71.52357)   
2     POINT (-71.52360 44.04124)   (44.04124, -71.5236)   
3     POINT (-71.52364 44.04127)  (44.04127, -71.52364)   
4     POINT (-71.52368 44.04127)  (44.04127, -71.52368)   
...                          ...                    ...   
4115  POINT (-71.52389 44.04126)  (44.04126, -71.52389)   
4116  POINT (-71.52384 44.04126)  (44.04126, -71.52384)   
4117  POINT (-71.52381 44.04127)  (44.04127, -71.52381)   
4118  POINT (-71.52366 44.04128)  (44.04128, -71.52366)   
4119  POINT (-71.52362 44.04126)  (44.04126, -71.52362)   

               end_lat_long  start_coverage  end_coverage  step_length  \
0     (44.04123, -71.52357)               1           1.0     2.404519   
1      (44.04124, -71.5236)               1           1.0     2.648834   
2     (44.04127, -71.52364)               1           1.0     4.624942   
3     (44.04127, -71.52368)               1           1.0     3.206023   
4     (44.04127, -71.52373)               1           1.0     4.007529   
...                     ...             ...           ...          ...   
4115  (44.04126, -71.52384)               1           1.0     4.007529   
4116  (44.04127, -71.52381)               1           1.0     2.648833   
4117  (44.04128, -71.52366)               1           1.0    12.073822   
4118  (44.04126, -71.52362)               1           1.0     3.900901   
4119   (44.04123, -71.5236)               1           1.0     3.698803   

      dist_traveled  
0          2.404519  
1          5.053353  
2          9.678295  
3         12.884318  
4         16.891847  
...             ...  
4115   15072.798689  
4116   15075.447522  
4117   15087.521344  
4118   15091.422245  
4119   15095.121048  

[4120 rows x 11 columns]

In [56]:
# Get the total distance with the start and end point in coverage
dist_in_coverage = graft_merge[(graft_merge['start_coverage'] == 1) & (graft_merge['end_coverage'] ==1)]['step_length'].sum()

In [57]:
# Get the total distance with the start and end point out of coverage
dist_out_coverage = graft_merge[(graft_merge['start_coverage'] == 0) & (graft_merge['end_coverage'] ==0)]['step_length'].sum()

In [58]:
# Get the distance either entering coverage or leaving coverage
# There is no way to know exactly how much of this is in or out of coverage, so I'll split it in half and allocate to each group
coverage_split = graft_merge[(graft_merge['start_coverage'] != graft_merge['end_coverage'])]['step_length'].sum()

In [59]:
# allocate the split coverage 
dist_in_coverage = dist_in_coverage + coverage_split/2
dist_out_coverage = dist_out_coverage + coverage_split/2

In [60]:
# Get the total distance
total_dist = dist_in_coverage + dist_out_coverage
total_dist

15095.121048062487

In [61]:
# See how many miles is traveled
total_dist/1609.344

9.379673362601462

In [62]:
# Get the percentage of distance traveled in coverage
dist_in_coverage/total_dist

0.7607536928943999

In [63]:
# Get the percent of distance traveled out of coverage
dist_out_coverage/total_dist

0.23924630710560016

In [64]:
import plotly.express as px
# import pandas as pd

In [65]:
# Making a copy to silence the SettingWithCopyWarning while using this lambda function to create a text-based categorical
# For in or out of coverage
graft_merge = graft_merge.copy()
# A string categorical column ("in" or "out") is needed to fill in both colors properly on the route
graft_merge['in_out'] = graft_merge['start_coverage'].apply(lambda x: 'in_coverage' if x==1 else 'out_of_coverage')

In [67]:

# Visualize the route in and out of coverage 
############################################
# https://stackoverflow.com/questions/53233228/plot-latitude-longitude-from-csv-in-python-3-6


fig = px.scatter_mapbox(graft_merge, 
                        lat="Latitude", 
                        lon="Longitude", 
                        hover_name="start_coverage", 
                        hover_data=["start_coverage", "end_coverage",'Elevation', 'dist_traveled'],
                        color="in_out",
                        zoom=13, 
                        height=800,
                        width=800)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [41]:
# Look at visualizing the elevation 
###################################
# https://stackoverflow.com/questions/53233228/plot-latitude-longitude-from-csv-in-python-3-6


fig = px.scatter_mapbox(HancockDF, 
                        lat="Latitude", 
                        lon="Longitude", 
                        hover_name="Elevation", 
                        hover_data=["Latitude", "Longitude",'Elevation'],
                        color="Elevation",
                        zoom=13, 
                        height=800,
                        width=800)

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [ ]:
# # Get centroid from trail - not using this but saving for later
# s = gpd.GeoSeries(
#     graftonDF['geometry'], crs="EPSG:3857")
# trail_dis = gpd.GeoDataFrame(s).dissolve()
# trail_cent = trail_dis.to_crs('+proj=cea').centroid.to_crs(trail_dis.crs)[0]


# Verizon Coverage Map for Grafton County 
* Data downloaded from the FCC's Moble LTE Coverage Website
* Last updated May 15, 2021

In [68]:
#### Look at the Verizon coverage for Grafton County, NH
x1,y1,x2,y2 = poly['geometry'].total_bounds

m = folium.Map(tiles='openstreetmap')
m.fit_bounds([[y1, x1], [y2, x2]])
folium.GeoJson(poly['geometry']).add_to(m)
m

In [43]:
# https://python-visualization.github.io/folium/quickstart.html#Getting-Started
# https://gis.stackexchange.com/questions/378431/mapping-multiple-polygons-on-folium

In [44]:
# https://stackoverflow.com/questions/58162200/pre-determine-optimal-level-of-zoom-in-folium
# Getting the southwest and northeast corners to plug into fit_bounds to focus the map on the trail
sw = graft_merge[['Latitude', 'Longitude']].min().values.tolist()
ne = graft_merge[['Latitude', 'Longitude']].max().values.tolist()


# Overlay the hiking route with the Verizon coverage map.

In [45]:
## Look at the route with the coverage to 

x1,y1,x2,y2 = poly['geometry'].total_bounds


m = folium.Map(tiles='openstreetmap')
m.fit_bounds([[y1, x1], [y2, x2]])
folium.GeoJson(poly['geometry']).add_to(m)
folium.PolyLine(graft_merge['start_lat_long'], tooltip="Hancock Trail",color='red').add_to(m)
m.fit_bounds([sw, ne])
m

In [ ]:
##################################################################################################
### Next get the elevation while on different parts of the hike
### and use a formula to estimate hiking speed based on elevation during certain parts of the hike
### Maybe add a slider for someone to enter about how fast of a hiker they are.


In [ ]:
## Tobler's function for hiking speed
# https://rpubs.com/chrisbrunsdon/hiking